[![Binder](img/badge-binder.svg)](https://mybinder.org/v2/gh/nhirschey/teaching/gh-pages?filepath=assignment-volatility-timing.ipynb)&emsp;
[![Script](img/badge-script.svg)](/Teaching//assignment-volatility-timing.fsx)&emsp;
[![Notebook](img/badge-notebook.svg)](/Teaching//assignment-volatility-timing.ipynb)

Student Name | Student Number
--- | ---
**1: Omar Ben Ayed** | 38628 &#32;
**2: Nicholas Sistovaris** | 49606 &#32;


This is an assignment. You may work in pairs (two students).  You will find sections labeled **Task** asking you to do each piece of analysis. Please make sure that you complete all of these tasks. I included some tests to help you see if you are calculating the solution correctly, but if you cannot get the test to pass submit your best attempt and you may recieve partial credit.

All work that you submit should be your own. Make use of the course resources and example code on the course website. It should be possible to complete all the requested tasks using information given below or somewhere on the course website.



In [ ]:
#r "nuget:FSharp.Data"
#r "nuget: FSharp.Stats"
#r "nuget: Plotly.NET, 2.0.0-preview.17"


Microsoft.DotNet.Interactive.InstallPackagesMessage


In [ ]:
#r "nuget: Plotly.NET.Interactive, 2.0.0-preview.17"


Microsoft.DotNet.Interactive.InstallPackagesMessage


In [ ]:
open System
open FSharp.Data
open Plotly.NET
open FSharp.Stats


for testing.



In [ ]:
#r "nuget: FsUnit.Xunit"
#r "nuget: xunit, 2.*"
open Xunit
open FsUnit.Xunit
open FsUnitTyped


Error: xunit version 2.* cannot be added because version 2.4.1 was added previously.

In [ ]:
// Set dotnet interactive formatter to plaintext
Formatter.Register(fun (x:obj) (writer: TextWriter) -> fprintfn writer "%120A" x )
Formatter.SetPreferredMimeTypesFor(typeof<obj>, "text/plain")
// Make plotly graphs work with interactive plaintext formatter
Formatter.SetPreferredMimeTypesFor(typeof<GenericChart.GenericChart>,"text/html")


## Load Data

First, make sure that you're referencing the correct files.

Here I'm assuming that you have a class folder with this
notebook and these files in it. The folder hierarchy would
look like below where you have the below files and folders accessible.

* `Common.fsx` is on the course website.

* `notebook.ipynb` is this notebook.

```code
/class
    Common.fsx
    notebook.ipynb                
```


In [ ]:
let [<Literal>] ResolutionFolder = __SOURCE_DIRECTORY__
Environment.CurrentDirectory <- ResolutionFolder

#load "Common.fsx"
open Common


We get the Fama-French 3-Factor asset pricing model data.



In [ ]:
let ff3 = 
    French.getFF3 Frequency.Daily
    |> Seq.toList
    |> List.filter (fun x -> x.Date < DateTime(2022,3,1))

let annualizeDailyStdDev dailyStdDev = sqrt(252.0) * dailyStdDev


As an example, I'll first calculate the standard deviation of the `MktRf` factor and assign it to a value named `stdDevMkt`.



In [ ]:
let stdDevMkt =
    ff3
    |> Seq.stDevBy (fun x -> x.MktRf)


The following test will pass if I calculate it correctly.



In [ ]:
// Test.
stdDevMkt 
|> should (equalWithin 0.005) 0.01


The test following test will fail if I calculate it incorrectly. In this failing example I report an annualized standard deviation instead of a daily standard deviation.



In [ ]:
let stdDevMktFAIL =
    ff3
    |> Seq.stDevBy (fun x -> x.MktRf)
    |> annualizeDailyStdDev

// Test
if false then // make this `if true` to run the test.
    stdDevMktFAIL
    |> should (equalWithin 0.005) 0.01


## Start of the assignment

> **Task:** Calculate the standard deviation of the `Hml` factor's daily returns. Assign it to a value named `stdDevHml`.
> 

Write your solution in the cell below.



In [ ]:
// Solution here
let stdDevHml =
    ff3
    |> Seq.stDevBy (fun x -> x.Hml)

// Test
stdDevHml 
|> should (equalWithin 0.005) 0.006


> **Task:** Calculate the annualized standard deviation of the `Hml` factor's daily returns. Assign it to a value named `stdDevHmlAnnualized`.
> 

Write your solution in the cell below.



In [ ]:
// Solution here
let stdDevHmlAnnualized =
    stdDevHml
    |> annualizeDailyStdDev

// Test
stdDevHmlAnnualized
|> should (equalWithin 0.005) 0.098


In [ ]:
stdDevHmlAnnualized

0.09811937527


> **Task:** Assign the daily returns of the `Hml` factor to a value named `hml` that is a `list` of `ReturnObs`.
> 



In [ ]:
type ReturnObs = 
    { 
        Name: string
        Date: DateTime 
        Return: float 
    }


Write your solution in the cell below.



In [ ]:
// Solution here
let hml =
    ff3
    |> List.map(fun x ->
        { Name = "hml"
          Date = x.Date
          Return = x.Hml})

// Tests
hml[..1] |> should be ofExactType<list<ReturnObs>>

hml[0].Name |> shouldEqual "hml"

hml |> shouldHaveLength 25187

hml
|> List.averageBy (fun x -> x.Return)
|> should (equalWithin 0.0001) 0.00015


> **Task:** Calculate the daily returns of the `Hml` factor with `2x` leverage applied to the portfolio every day. Assign it to a value named `hml2x` that is a `list` of `ReturnObs`.
> 

Write your solution in the cell below.



In [ ]:
// Solution here
let hml2x =
    ff3
    |> List.map(fun x ->
        { Name = "hml2x"
          Date = x.Date
          Return = x.Hml*2.0}) //adding the leverage


// Tests
hml2x[..1] |> should be ofExactType<list<ReturnObs>>

hml2x[0].Name |> shouldEqual "hml2x"

hml2x |> shouldHaveLength 25187

hml2x
|> List.averageBy (fun x -> x.Return)
|> should (equalWithin 0.0001) 0.0003


> **Task:** Calculate the average annualized daily return of the `Hml` factor and assign it to a value name `hmlAvg`.
> 

Write your solution in the cell below.



In [ ]:
// solution here
let annualizeDaily x = 252.0 * x

let hmlAvg =
    ff3
    |> List.averageBy(fun x -> x.Hml)
    |> annualizeDaily

// tests
hmlAvg |> should (equalWithin 0.005) 0.04


> **Task:** Calculate the average annualized daily return of the 2x leveraged `Hml` factor and assign it to a value name `hml2xAvg`.
> 

Write your solution in the cell below.



In [ ]:
// solution here
let hml2xAvg = 
    hml2x
    |> List.map(fun x -> x.Return |> annualizeDaily)
    |> List.average

// tests
hml2xAvg |> should (equalWithin 0.005) 0.075


Here is some code that you will use for the next task.



In [ ]:
type GrowthObs =
    { 
        Name: string
        Date: DateTime
        Growth: float
    }

let cumulativeGrowth (xs: list<ReturnObs>) =
    let sorted = xs |> List.sortBy (fun x -> x.Date)
    let calcGrowth (prior: GrowthObs) (current: ReturnObs) =
        { Name = current.Name 
          Date = current.Date
          Growth = prior.Growth * (1.0 + current.Return) }        
    match sorted with
    | [] -> []
    | h::t ->
        let firstOb = 
            { Name = h.Name 
              Date = h.Date
              Growth = 1.0 + h.Return }
        (firstOb, t) ||> List.scan calcGrowth


> **Task:** Calculate the cumulative growth of $1 invested in HML at the start of the sample. Assign it to a value named `hmlGrowth` that is a `list` of `GrowthObs`.
> 

Write your solution in the cell below.



In [ ]:
// Solution here
let hmlGrowth =
    hml 
    |> cumulativeGrowth

// Tests
hmlGrowth[..1] |> should be ofExactType<list<GrowthObs>>

hmlGrowth
|> List.map (fun x -> x.Growth)
|> List.last
|> should (equalWithin 1.0) 27.0


> **Task:** Calculate the cumulative growth of $1 invested in 2x levered HML at the start of the sample. Assign it to a value named `hml2xGrowth` that is a `list` of `GrowthObs`.
> 

Write your solution in the cell below.



In [ ]:
// Solution here
let hml2xGrowth =
    hml2x
    |> cumulativeGrowth

// Tests
hml2xGrowth[..1] |> should be ofExactType<list<GrowthObs>>

hml2xGrowth
|> List.map (fun x -> x.Growth)
|> List.last
|> should (equalWithin 1.0) 286.0


In [ ]:
let stdDevHml2xAnnualized =
    ff3
    |>

Here is an example of a plot of the cumulative growth of $1 invested in the market.



In [ ]:
let mkt = 
    [ for x in ff3 do
        { Name = "market"
          Date = x.Date
          Return = x.MktRf } ]

let marketGrowthChart = 
    mkt
    |> cumulativeGrowth
    |> List.map (fun x -> x.Date, x.Growth)
    |> Chart.Line
    |> Chart.withYAxisStyle (AxisType = StyleParam.AxisType.Log)


In [ ]:
marketGrowthChart


<!-- Plotly chart will be drawn inside this DIV -->

> **Task:** Plot the cumulative growth of $1 invested in HML and $1 invested in the Market as a combined line chart using a log scale for the y-axis.
> 

Write your solution in the cell below.



In [ ]:
// Solution here
let hmlGrowthChart =
    hmlGrowth
    |> List.map (fun x -> x.Date, x.Growth)
    |> Chart.Line
    |> Chart.withYAxisStyle(AxisType = StyleParam.AxisType.Log)

let growthToPlot = [hmlGrowthChart ; marketGrowthChart]

growthToPlot |> Chart.combine
    

<!-- Plotly chart will be drawn inside this DIV -->

> **Task:** Apply a constant levarage to the HML and market factors for the full sample such that the daily returns have a full-sample annualized standard deviation equal to 10%. Assign the results to values named `hml10` and `mkt10` that are lists of `ReturnObs`.
> 

Write your solution in the cell below.



In [ ]:
// Solution here
let stdDevMktAnnualized = 
    stdDevMkt 
    |> annualizeDailyStdDev

let hml10 =
    let HMLweight = (0.1 / stdDevHmlAnnualized)
    [for x in ff3 do
        { Name = "hml10"
          Date = x.Date
          Return = x.Hml * HMLweight}]

let mkt10 =
    let MKTweight = (0.1 / stdDevMktAnnualized)
    [for x in ff3 do
        { Name = "mkt10"
          Date = x.Date
          Return = x.MktRf * MKTweight}]

// Tests
hml10[..1] |> should be ofExactType<list<ReturnObs>>
mkt10[..1] |> should be ofExactType<list<ReturnObs>>

hml10 
|> stDevBy (fun x -> x.Return) 
|> annualizeDailyStdDev
|> should (equalWithin 1e-6) 0.1

mkt10
|> stDevBy (fun x -> x.Return) 
|> annualizeDailyStdDev
|> should (equalWithin 1e-6) 0.1


In [ ]:
stdDevMktAnnualized

0.1709622644


> **Task:** Plot the cumulative growth of $1 invested in `hml10` and `mkt10` as a combined line chart using a log scale for the y-axis.
> 

Write your solution in the cell below.



In [ ]:
// Solution here
let mkt10GrowthChart = 
    mkt10
    |> cumulativeGrowth
    |> List.map (fun x -> x.Date, x.Growth)
    |> Chart.Line
    |> Chart.withYAxisStyle (AxisType = StyleParam.AxisType.Log)

let hml10GrowthChart =
    hml10
    |> cumulativeGrowth
    |> List.map (fun x -> x.Date, x.Growth)
    |> Chart.Line
    |> Chart.withYAxisStyle(AxisType = StyleParam.AxisType.Log)

let growthToPlot = [hml10GrowthChart ; mkt10GrowthChart]

growthToPlot |> Chart.combine


<!-- Plotly chart will be drawn inside this DIV -->

> **Task:** Explain how to intepret the dramatic difference between the two plots that you have just created. Why is the plot of $1 invested in unlevered HML and Market factors so different from the plot of $1 invested in the versions that are levered to have a 10% annualized standard deviation?
> 

The unlevered Market and HML standard deviations were 17.09% and 9.81% respectively. 
This explains why the HML returns remained approximately the same, since the leverage leads to approximately the same standard deviation.
The Market standard deviation was delevered meaning that returns dropped to around the same as the HML portfolio. However, the returns still remain higher than the HML ones.
What we can conclude is that the extra market returns where due to the undertaking of more risk in the market portfolio.

